# Cycling data 3. Maps - plot .fit file on map using folium

### Contents
0. Install fitparse and python libraries
1. Parse the fit file and read into Pandas dataframe
2. Data cleaning
3. Show data on a map using folium
4. Show a map using GeoPandas


#### To do:
- [ ] convert points to polyline (https://deparkes.co.uk/2016/06/03/plot-lines-in-folium/)
- [ ] polyline/points different colors based on value (https://stackoverflow.com/questions/42756934/how-to-plot-lat-and-long-from-pandas-dataframe-on-folium-map-group-by-some-label)
- [ ] create midpoint out of a group of points to centralize the map
- [ ] also to find start/endpoint based on given point
- [ ] show segment in table + on map


## 0. Install fitparse and import the python libraries

We use the fitparse library to parse the .fit file.

Please find the github of fitparse project here: http://dtcooper.github.io/python-fitparse/

In [1]:
!pip install fitparse 

In [2]:
#import the modules
import numpy as np
import pandas as pd
import fitparse

## 1. import the .fit file and read it into pandas dataframe


In [3]:
# parse the fit file and read it into a list called workout
#source: http://johannesjacob.com/
from fitparse import FitFile
import pandas as pd
import matplotlib.pyplot as plt

fitfile = FitFile('39094458.fit') ### enter the name of the file here!

while True:
    try:
        fitfile.messages
        break
    except KeyError:
        continue
workout = []
for record in fitfile.get_messages('record'):
    r = {}
    for record_data in record:
        r[record_data.name] = record_data.value
    workout.append(r)

In [4]:
#read this list into a pandas dataframe
fietsdata = pd.DataFrame(workout)
fietsdata.head()

accumulated_power  altitude  cadence  calories  distance  \
0            15931.0      2455     71.0         0      15.0   
1            15931.0      2455     71.0         0      15.0   
2            16088.0      2455     71.0         0      28.0   
3            16088.0      2455     71.0         0      28.0   
4            16626.0      2455     71.0         1      43.0   

   enhanced_altitude  enhanced_speed grade  heart_rate left_pedal_smoothness  \
0               -9.0           6.337  None         121                  None   
1               -9.0           6.312  None         121                  None   
2               -9.0           6.497  None         121                  None   
3               -9.0           7.202  None         121                  None   
4               -9.0           7.089  None         122                  None   

  left_right_balance left_torque_effectiveness  position_lat  position_long  \
0               None                      None     624664830       57966729   
1               None                      None     624664612       57965695   
2               None                      None     624664433       57964502   
3               None                      None     624664254       57963090   
4               None                      None     624664035       57961857   

   power right_pedal_smoothness right_torque_effectiveness  speed  \
0  111.0                   None                       None   6337   
1  157.0                   None                       None   6312   
2  147.0                   None                       None   6497   
3  122.0                   None                       None   7202   
4  144.0                   None                       None   7089   

   temperature           timestamp  
0           21 2020-04-27 07:57:13  
1           21 2020-04-27 07:57:14  
2           21 2020-04-27 07:57:15  
3           21 2020-04-27 07:57:16  
4           21 2020-04-27 07:57:17

In [1]:
#check data
fietsdata.dtypes

NameError: name 'fietsdata' is not defined

## 2. Data cleaning: convert semicircles to degrees

Bike computers store geodata commonly as semicircles as this improve storage capacity. 
To use this data, we need to convert it from semicircles to degrees.

We can use the following formula: degrees = semicircles * (180 / 2 ** 31)

In [6]:
#Convert position_long and position_lat from semicircles to degrees
fietsdata['pos_lat'] = fietsdata['position_lat']*  (180 / 2**31)
fietsdata['pos_long'] = fietsdata['position_long']*  (180 / 2**31)
fietsdata.head()

accumulated_power  altitude  cadence  calories  distance  \
0            15931.0      2455     71.0         0      15.0   
1            15931.0      2455     71.0         0      15.0   
2            16088.0      2455     71.0         0      28.0   
3            16088.0      2455     71.0         0      28.0   
4            16626.0      2455     71.0         1      43.0   

   enhanced_altitude  enhanced_speed grade  heart_rate left_pedal_smoothness  \
0               -9.0           6.337  None         121                  None   
1               -9.0           6.312  None         121                  None   
2               -9.0           6.497  None         121                  None   
3               -9.0           7.202  None         121                  None   
4               -9.0           7.089  None         122                  None   

   ... position_lat position_long  power  right_pedal_smoothness  \
0  ...    624664830      57966729  111.0                    None   
1  ...    624664612      57965695  157.0                    None   
2  ...    624664433      57964502  147.0                    None   
3  ...    624664254      57963090  122.0                    None   
4  ...    624664035      57961857  144.0                    None   

   right_torque_effectiveness speed temperature           timestamp  \
0                        None  6337          21 2020-04-27 07:57:13   
1                        None  6312          21 2020-04-27 07:57:14   
2                        None  6497          21 2020-04-27 07:57:15   
3                        None  7202          21 2020-04-27 07:57:16   
4                        None  7089          21 2020-04-27 07:57:17   

     pos_lat  pos_long  
0  52.358801  4.858715  
1  52.358783  4.858628  
2  52.358768  4.858528  
3  52.358753  4.858410  
4  52.358735  4.858307  

[5 rows x 22 columns]

## 3. Show data on map

### 3a. Use folium to create a base map

In [7]:
# uncomment when you've never used folium before
#! pip install folium   

In [8]:
import folium

cycle_map = folium.Map(location=[52.373,4.890],  #amsterdammers believe their city is the center of the world but feel free to change the coordinates to your liking ;-)
                  tiles='Stamen Terrain', # choose Stamen Terrain as base map or use another
                  zoom_start=10, # zoom level. Lower = zoom out; higher = zoom in
                  detect_retina=True) # optional, used to detect high quality screes

cycle_map

### 3b. Remove all unnecessary data; just keep the lat, long.

In [10]:
# print the columns
fietsdata.columns

Index(['accumulated_power', 'altitude', 'cadence', 'calories', 'distance',
       'enhanced_altitude', 'enhanced_speed', 'grade', 'heart_rate',
       'left_pedal_smoothness', 'left_right_balance',
       'left_torque_effectiveness', 'position_lat', 'position_long', 'power',
       'right_pedal_smoothness', 'right_torque_effectiveness', 'speed',
       'temperature', 'timestamp', 'pos_lat', 'pos_long'],
      dtype='object')

In [12]:
# remove all columns except 'pos_lat' and 'pos_long'
coor = fietsdata.drop(['accumulated_power', 'altitude', 'cadence', 'calories', 'distance',
       'enhanced_altitude', 'enhanced_speed', 'grade', 'heart_rate',
       'left_pedal_smoothness', 'left_right_balance',
       'left_torque_effectiveness', 'position_lat', 'position_long', 'power',
       'right_pedal_smoothness', 'right_torque_effectiveness', 'speed',
       'temperature', 'timestamp'], axis=1) # drop NaN
coor_valid = coor[coor.pos_lat != 'None'] # drop None
coor_valid

C:\Users\Michiel\Anaconda3\lib\site-packages\pandas\core\ops\__init__.py:1115: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  result = method(y)


pos_lat  pos_long
0      52.358801  4.858715
1      52.358783  4.858628
2      52.358768  4.858528
3      52.358753  4.858410
4      52.358735  4.858307
...          ...       ...
12292  52.358830  4.861727
12293  52.358821  4.861737
12294  52.358816  4.861750
12295  52.358823  4.861755
12296  52.358818  4.861755

[12297 rows x 2 columns]

### 3c. Plot the coordinates on the map

In [14]:
import folium

coor_valid.apply(lambda row:folium.Circle(radius=10, location=[row["pos_lat"], 
                                                  row["pos_long"]]).add_to(cycle_map),
                axis=1)
cycle_map.add_child(folium.LatLngPopup())
cycle_map

In [1]:
cycle_map.save('cycle_map.html') # save the map as an html file

NameError: name 'cycle_map' is not defined

## 4. Plot on a map using GeoPandas

GeoPandas is a different library for map plotting. It's not as nice as folium but widely used so we'll try it out here. 

In [ ]:
# We will use GeoPandas module. See my tutorial on maps for more info.

import geopandas as gpd

fiets_gpf = gpd.GeoDataFrame(fietsdata, geometry= gpd.points_from_xy(fietsdata['long'], fietsdata['lat']))
fiets_gpf.head()

In [ ]:
fiets_gpf.plot()
# Plot the x,y coordinates

## 5. Segments  - WORK IN PROGRESS

Use the map above to select a start point and endpoint close to your route.

Code: 
Input:
-  enter start point Latitude: 52.3559 Longitude: 4.9681
-  enter last point Latitude: 52.3570 Longitude: 4.9706

Logic:
- find nearest points on route based on point class example for start/end points

Return
- Return data for this segment:
    - time, speed, heart_rate, power, cadence
- show in graph


In [ ]:
# Input: ask the user to specify the segment.

segment_name = input("Enter name of segment")

startpoint_lat = float(input("Enter lat of startpoint"))
startpoint_long = float(input("Enter long of startpoint"))

endpoint_lat = float(input("Enter lat of startpoint"))
endpoint_long = float(input("Enter long of end point"))

print(segment_name)
print("startpoint="+ str(startpoint_lat) +str(startpoint_long))
print("endpoint=" + str(endpoint_lat) + str(endpoint_long))


Enter name of segmentmihiel
